## Plot the violations on a map

- Use the folium module to put a marker at every latitude and longitude where a traffic violation occurred.

conda install -c conda-forge folium

In [1]:
import folium

openFile = open('Traffic_Violations-filtered.csv')

# Iterate through every line in the file.

minLat = 999
maxLat = 0
minLong = 999
maxLong = -999

coords = []
makeModels = []

for line in openFile:
    if line.startswith('Date Of Stop'):
        continue
        
    columns = line.split('|')
    try:
        lat = float(columns[6])
        # There are some outlier (presumably erroneous) coordinates.
        if lat > 38.0 and lat < 42.0:
            if lat < minLat:
                minLat = lat
            elif lat > maxLat:
                maxLat = lat
    except ValueError as err:
        lat = None
    try:
        long = float(columns[7])
        if long > -79.0 and long < -76.0:
            if long < minLong:
                minLong = long
            elif long > maxLong:
                maxLong = long
            
    except ValueError as err:
        long = None
        
    if lat and long:
        coords.append((lat, long))
        if columns[21]:
            make = columns[21]
        else:
            make = 'Unknown'
        makeModels.append(make)
        # With too much data the map won't render.
        # makeModels.append('{} {}'.format(columns[21], columns[22]))
    

openFile.close()

print('Found', len(coords), 'coordinates')
print('Latitudes: {:6.3f} to {:6.3f}'.format(minLat, maxLat))
print('Longitudes: {:6.3f} to {:6.3f}'.format(minLong, maxLong))


Found 54317 coordinates
Latitudes: 38.855 to 39.701
Longitudes: -77.568 to -76.346


In [3]:
# Fudge where the center is -- not sure why this is needed

startLat = maxLat - ((2 / 3) * (maxLat - minLat))
startLong = maxLong - ((2 / 3) * (maxLong - minLong))

m = folium.Map(location=[startLat, startLong],
               zoom_start=10)

for count, (lat, long) in enumerate(coords):
    # Only plot every 10th coordinate pair
    # to keep the map looking simple
    if count % 10 == 0:
        folium.CircleMarker(location=[lat, long],
                            radius=1,
                            opacity=0.5,
                            popup=makeModels[count],
                            color='#3186cc').add_to(m)

m